## Choropleth maps with county data
Note the Choropleth class is not used in this example, instead a map styling function is used to color the counties in topojson. Several examples are in the quick start guide 
https://python-visualization.github.io/folium/quickstart.html#Styling-function 
The first example is modified to show color map and shown below

In [ ]:
#Example code from GeoJSON and choropleth
import numpy as np
import pandas as pd
import folium
import os
import branca

county_data = os.path.join('data', 'us_county_data.csv')
county_geo = os.path.join('data', 'us_counties_20m_topo.json')

df = pd.read_csv(county_data, na_values=[' '])

#Colorscale goes from 0 to 80000
colorscale = branca.colormap.linear.YlOrRd_09.scale(0, 80e3)
employed_series = df.set_index('FIPS_Code')['Employed_2011']


def style_function(feature):
    employed = employed_series.get(int(feature['id'][-5:]), None)
    return {
        'fillOpacity': 0.5,
        'weight': 0,
        'fillColor': '#black' if employed is None else colorscale(employed)
    }


m = folium.Map(
    location=[48, -102],
    tiles='cartodbpositron',
    zoom_start=3
)

folium.TopoJson(
    open(county_geo),
    'objects.us_counties_20m',
    style_function=style_function
).add_to(m)

colorscale.caption = 'Number employed'
colorscale.add_to(m)


m

# Downloaded data from USDA
Here is an example using data downloaded from USDA.

https://www.ers.usda.gov/data-products/county-level-data-sets/download-data/


In [ ]:
import numpy as np
import pandas as pd
import folium

#Load the data as dataframe, select a series and display header 
#note that the dropna() drops any missing values 
df = pd.read_excel("data/PovertyEstimatesCounties.xls", 
                    sheet_name="Poverty Data 2016", skiprows=range(3))

#Create a poverty data set using percent poverty for 2016
poverty_series = df.set_index('FIPStxt')['PCTPOVALL_2016'].dropna()
df.head()
#poverty_series.head()

In [ ]:
import branca
colorscale = branca.colormap.linear.YlOrRd_09.scale(0, 50)

us_map = folium.Map(location=[39,-98], zoom_start=4)
county_geo = 'data/us_counties_20m_topo.json'

def style_function(feature):
    percent = poverty_series.get(int(feature['id'][-5:]), None)
    return {
        'fillOpacity': 0.5,
        'weight': 0,
        'fillColor': 'white' if percent is None else colorscale(percent)

    }

#Create a choropleth map using TopoJson Class
folium.TopoJson(
    open(county_geo),
    'objects.us_counties_20m',
    style_function=style_function
).add_to(us_map)

#create a legend for the colormap
colorscale.caption = 'Poverty color scale (%)'
colorscale.add_to(us_map)


us_map

# Use choropleth class instead

In [ ]:
us_map = folium.Map(location=[39,-98], zoom_start=4)
county_geo = 'data/us_counties_geo.json'

folium.Choropleth(
    geo_data=county_geo, 
).add_to(us_map)


us_map

In [ ]:
#Try with a 20m resolution topo json, but no luck 
us_map = folium.Map(location=[39,-98], zoom_start=4)
county_geo = 'data/us_counties_20m_topo.json'

#https://python-visualization.github.io/folium/modules.html#folium.features.Choropleth
folium.Choropleth(
    geo_data=county_geo, 
    #topojson='objects.us_counties_20m'
).add_to(us_map)

us_map

In [ ]:
import numpy as np
import pandas as pd
import folium

#Load the data as dataframe, convert FIPS codes to string
df = pd.read_excel("data/PovertyEstimatesCounties.xls", converters={'FIPStxt':str},
                   sheet_name="Poverty Data 2016", skiprows=range(3))

us_map = folium.Map(location=[39,-98], zoom_start=4)

#note low resolution geojson with simple county polygons
county_geo = 'data/us_counties_geo.json'  #Geojson format

#higher 20m resolution geojson
#county_geo = 'data/cb_2014_us_county_20m.json'

#Use the Choropleth class
folium.Choropleth(
    geo_data=county_geo,
    data=df,
    columns=['FIPStxt','PCTPOVALL_2016'],
    key_on='feature.id',              #low res version
    #key_on='feature.properties.geoid', #20m res version
    fill_color='YlOrRd',
    fill_opacity = 0.5,
    legend_name='Poverty (%)'
).add_to(us_map)

us_map

Notice that the first 9 states are greyed out because 4 digit county codes are used

In [ ]:
#Load the data as dataframe
df = pd.read_excel("data/PovertyEstimatesCounties.xls", 
                   sheet_name="Poverty Data 2016", skiprows=range(3))

#Convert county codes after reading as integers, these now match json ids
df['FIPStxt']=df['FIPStxt'].astype(str)

us_map = folium.Map(location=[39,-98], zoom_start=4)

#note low resolution geojson with simple county polygons
county_geo = 'data/us_counties_geo.json'  #Geojson format

#Use the Choropleth class
folium.Choropleth(
    geo_data=county_geo,
    data=df,
    columns=['FIPStxt','PCTPOVALL_2016'],
    key_on='feature.id',              #low res version
    fill_color='YlOrRd',
    fill_opacity = 0.5,
    legend_name='Poverty (%)'
).add_to(us_map)

us_map

In [ ]:
import numpy as np
import pandas as pd
import folium

#Load the data as dataframe
county_data = os.path.join('data', 'us_county_data.csv')
df = pd.read_csv(county_data, na_values=[' '])

#drop state totals
df.drop( df[ df['FIPS_Code']%1000 == 0 ].index , inplace=True)

#convert to string, otherwise no codes match
df['FIPS_Code']=df['FIPS_Code'].astype(str)

us_map = folium.Map(location=[39,-98], zoom_start=4)
#county_geo = 'data/cb_2014_us_county_20m.json'
county_geo = 'data/us_counties_geo.json'  #Geojson format

#Use the Choropleth class
folium.Choropleth(
    geo_data=county_geo,
    data=df,
    columns=['FIPS_Code','Employed_2011'],
    key_on='feature.id',              #low res version
    #key_on='feature.properties.geoid', #20m res version
    colormap = colorscale,
    fill_color='YlOrRd',
    fill_opacity = 0.5,
    legend_name='Employed'
).add_to(us_map)

us_map